##### This is the SECOND (WITHOUT OUTLIERS) note book is meant to do the cross validation for the projecteed points

In [2]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from sklearn.linear_model import LinearRegression
from matplotlib import cm
import math
import seaborn as sns
import scipy

In [3]:
data_0 = pd.read_csv('predictions_df_west_5_wall_floor_0.csv')
print('Length of data frame {}'.format(len(data_0)))

Length of data frame 10000


In [4]:
data_0.head(3)

Unnamed: 0         X         Y         Z       N_X       N_Y       N_Z  \
0       77601  0.999975  0.999949  0.837766 -0.560243  0.825043 -0.075522   
1      226544  0.999992  0.999984  0.834851 -0.499940  0.866100  0.012123   
2      430760  0.999939  0.999876  0.902326  0.615117 -0.779994  0.116483   

  label  cat_label prediction_label ground_truth_label comparison  
0  wall          3             wall               wall      match  
1  wall          3             wall               wall      match  
2  wall          3             wall               wall      match

In [5]:
data_floor_subset_0 = data_0[['X','Y','Z']].loc[data_0.label =='floor']
data_wall_subset_0 = data_0[['X','Y','Z']].loc[data_0.label =='wall']


print('Length of data frame {}'.format(len(data_floor_subset_0)))


Length of data frame 5000


In [6]:
#removing the outliers
data_floor_subset_0 = data_floor_subset_0[data_floor_subset_0['Z']<0.983]

print('Length of data frame {}'.format(len(data_floor_subset_0)))

Length of data frame 4048


In [7]:
data_floor_subset_0['regression_parm'] = 1
data_floor_subset_0.head(2)

X         Y         Z  regression_parm
5000  0.999996  0.999970  0.969438                1
5001  0.999993  0.999971  0.969314                1

In [8]:
x_f= data_floor_subset_0['X'].to_numpy()      
y_f= data_floor_subset_0['Y'].to_numpy() 
z_f= data_floor_subset_0['Z'].to_numpy() 

In [9]:
x_w= data_wall_subset_0['X'].to_numpy()      
y_w= data_wall_subset_0['Y'].to_numpy() 
z_w= data_wall_subset_0['Z'].to_numpy() 

In [10]:
def calc_plane(x_f, y_f, z_f):
    a = np.column_stack((x_f, y_f, np.ones_like(x_f)))
    return np.linalg.lstsq(a, z_f)[0]


beta = calc_plane(x_f, y_f, z_f)
beta

<ipython-input-10-580085ab5359>:3: FutureWarning: `rcond` parameter will change to the default of machine precision times ``max(M, N)`` where M and N are the input matrix dimensions.
To use the future default and silence this warning we advise to pass `rcond=None`, to keep using the old, explicitly pass `rcond=-1`.
  return np.linalg.lstsq(a, z_f)[0]


array([-156.37403053,  -13.46028622,  170.80286376])

In [11]:
a_n =beta[0]
b_n =beta[1]
c_n =-1
d = beta[2]

In [12]:
def project_points(x, y, z, a, b, c):
    """
    Projects the points with coordinates x, y, z onto the plane
    defined by a*x + b*y + c*z = 1
    """
    vector_norm = a*a + b*b + c*c
    u = np.column_stack((x, y, z))
    n = np.array([a, b, c]) /np.sqrt(vector_norm)
    u_n_dot = np.dot(u,n[:,None])*n

    return u-u_n_dot

In [13]:
projected_points_floor = project_points(x_f, y_f, z_f, a_n, b_n, c_n)

In [14]:
x_proj_floor = projected_points_floor[:,0]
y_proj_floor = projected_points_floor[:,1]
z_proj_floor = projected_points_floor[:,2]

In [15]:
a= beta[0]
b= beta[1]
d= beta[2]

x1= x_f[:60] # original data        
y1= y_f[:60] # original data   

X1,Y1 = np.meshgrid(x1,y1)
Z1= (a * X1 ) + (b * Y1) +(d) # regression equation to estimate z


In [16]:
import plotly.graph_objects as go
scatter_floor_org = go.Scatter3d(x = x_f,y = y_f,z = z_f,mode='markers',
    marker=dict(
        size=1,
        color='green',
        opacity=0.7))

scatter_wall_org = go.Scatter3d(x = x_w,y = y_w,z = z_w,mode='markers',
    marker=dict(
        size=1,
        color='red',
        opacity=0.7))   


import plotly.graph_objects as go
fig1 = go.Figure(data=[scatter_floor_org])

fig1.update_layout(
    title='Floor and Wall Points Original',
    scene=dict(
        xaxis_title='X-axis',
        yaxis_title='Y-axis',
        zaxis_title='Z-axis',
    ),
)

# Show the plot
fig1.show()

In [17]:
import plotly.graph_objects as go
surface = go.Surface(z=Z1, x=X1, y=Y1)
scatter_floor_org = go.Scatter3d(x = x_f,y = y_f,z = z_f,mode='markers',
    marker=dict(
        size=1,
        color='green',
        opacity=0.7))

In [18]:
import plotly.graph_objects as go
fig2 = go.Figure(data=[surface, scatter_floor_org])

fig2.update_layout(
    title='Surface Plot with Scatter Overlay -Floor Original',
    scene=dict(
        xaxis_title='X-axis',
        yaxis_title='Y-axis',
        zaxis_title='Z-axis',
    ),
)

# Show the plot
fig2.show()

In [19]:
a_d= beta[0]
b_d= beta[1]
c_d= -1
d = beta[2]

v = np.array([a_d,b_d,c_d])
n_unit_vector = v / np.sqrt(np.sum(v**2))

In [20]:
dis = abs(d /(math.sqrt(a_d*a_d + b_d*b_d +c_d*c_d)))
dis

1.0882250461564262

In [21]:
fin_x_proj_floor = x_proj_floor-dis*n_unit_vector[0]
fin_y_proj_floor = y_proj_floor-dis*n_unit_vector[1]
fin_z_proj_floor= z_proj_floor-dis*n_unit_vector[2]

In [22]:
scatter_proj = go.Scatter3d(x = fin_x_proj_floor,y = fin_y_proj_floor,z = fin_z_proj_floor,mode='markers',
    marker=dict(
        size=1,
        color='green',
        opacity=0.7))

In [23]:
import plotly.graph_objects as go
fig_3 = go.Figure(data=[scatter_proj])

fig_3.update_layout(
    title='Scatter plot - Projected Floor Points',
    scene=dict(
        xaxis_title='X-axis',
        yaxis_title='Y-axis',
        zaxis_title='Z-axis',
    ),
)

# Show the plot
fig_3.show()

In [24]:
a_d= beta[0]
b_d= beta[1]
c_d= -1
d = beta[2]

v = np.array([a_d,b_d,c_d])
n_unit_vector = v / np.sqrt(np.sum(v**2))

In [25]:
dis = abs(d /(math.sqrt(a_d*a_d + b_d*b_d +c_d*c_d)))
dis

1.0882250461564262

In [26]:
import plotly.graph_objects as go
surface = go.Surface(z=Z1, x=X1, y=Y1)

fig_4 = go.Figure(data=[surface,scatter_proj])

fig_4.update_layout(
    title='Surface Plot with Projected Floor points Overlay',
    scene=dict(
        xaxis_title='X-axis',
        yaxis_title='Y-axis',
        zaxis_title='Z-axis',
))

# Show the plot
fig_4.show()

Wall Points

In [27]:
x_w= data_wall_subset_0['X'].to_numpy()           
y_w= data_wall_subset_0['Y'].to_numpy()  
z_w =(a * x_w ) + (b * y_w) +(d)
#z_w= data_wall_subset_0['Z'].to_numpy() 

In [28]:
#projected_points_wall= project_points(x_w, y_w, z_w, a_n, b_n, c_n)
projected_points_wall= project_points(x_w[:4800], y_w[:4800], z_w[:4800], a_n, b_n, c_n)

In [29]:
x_proj_wall = projected_points_wall[:,0]
y_proj_wall = projected_points_wall[:,1]
z_proj_wall = projected_points_wall[:,2]

In [30]:
fin_x_proj_wall = x_proj_wall-dis*n_unit_vector[0]
fin_y_proj_wall = y_proj_wall-dis*n_unit_vector[1]
fin_z_proj_wall = z_proj_wall-dis*n_unit_vector[2]

In [31]:
import plotly.graph_objects as go

scatter_floor_org =go.Scatter3d(x=x_f, y=y_f, z=z_f,mode='markers',
    marker=dict(
        size=1,
        color='green',
        opacity=0.7))

scatter_wall_org =go.Scatter3d(x=x_w, y=y_w, z=z_w,mode='markers',
    marker=dict(
        size=1,
        color='red',
        opacity=0.7))


scatter_wall_proj= go.Scatter3d(x=fin_x_proj_wall, y=fin_y_proj_wall, z=fin_z_proj_wall,mode='markers',
    marker=dict(
        size=1,
        color='cyan',
        opacity=0.7))



In [32]:
import plotly.graph_objects as go
fig_5 = go.Figure(data=[scatter_proj,scatter_wall_org,surface,scatter_wall_proj])

fig_5.update_layout(
    title='Scatter plot - Projected Wall and Floor Points on Plane ',
    scene=dict(
        xaxis_title='X-axis',
        yaxis_title='Y-axis',
        zaxis_title='Z-axis',
    ),
)

# Show the plot
fig_5.show()

In [33]:
#projected_points_wall[0]
wall_org = np.c_[x_w,y_w,z_w]
vec = wall_org[1] -projected_points_wall[1]

vec[0]/a_n,vec[1]/b_n,vec[2]/c_n


(-0.006933336625640674, -0.0069333366256406756, -0.0069333366256406626)

In [34]:
import plotly.graph_objects as go
#fig82 = go.Figure(data=[scatter_proj,scatter_wall_proj])
fig82 = go.Figure(data=[scatter_proj])
#fig7 = go.Figure(data=[scatter_floor_org,scatter_wall_org,surface,scatter_floor_proj])

#fig7 = go.Figure(data=[scatter_floor_proj,surface,scatter_wall_proj,])

fig82.update_layout(
    title='Projected Points -Wall and Floor',
    scene=dict(
        xaxis_title='X-axis',
        yaxis_title='Y-axis',
        zaxis_title='Z-axis',
    ),
)

# Show the plot
fig82.show()

#### Heatmap
##### --- Original Data

In [35]:

fig7 = go.Figure(data=[scatter_floor_org,scatter_wall_org])

fig7.update_layout(
    title='Floor and Wall Points Original',
    scene=dict(
        xaxis_title='X-axis',
        yaxis_title='Y-axis',
        zaxis_title='Z-axis',
    ),
)

# Show the plot
fig7.show()

In [36]:
x_w_expt= data_wall_subset_0['X'].to_numpy()      
y_w_expt= data_wall_subset_0['Y'].to_numpy() 
z_w_expt= data_wall_subset_0['Z'].to_numpy() 

In [40]:
type(fin_x_proj_wall)

numpy.ndarray

In [45]:
df_wall_final = pd.DataFrame({'x': fin_x_proj_wall, 'y': fin_y_proj_wall, 'z': fin_z_proj_wall})


In [47]:
df_wall_final.to_csv('df_wall_final', index=False, sep=';', encoding='ISO-8859-1')


In [48]:
df_floor_final = pd.DataFrame({'x': fin_x_proj_floor, 'y': fin_y_proj_floor, 'z': fin_z_proj_floor})

In [49]:
df_floor_final.to_csv('df_floor_final', index=False, sep=';', encoding='ISO-8859-1')